In [59]:
from rdflib import Graph, URIRef, Namespace, Literal, XSD, RDF
from rdflib.plugins.stores.sparqlstore import SPARQLStore
from tqdm.autonotebook import tqdm
import pandas as pd
from copy import deepcopy
import numpy
from sklearn.metrics.pairwise import cosine_similarity
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from collections import defaultdict
from rapidfuzz import process, fuzz, distance
import math

import torch
from transformers import BertTokenizer
from transformers import BertModel
from sklearn.metrics.pairwise import cosine_similarity

In [3]:
GRAPH_1_INV_FUNC_PATH = ''
GRAPH_1 = ""
GRAPH_2_INV_FUNC_PATH = ''
GRAPH_2 = ""
#GRAPH_2 = "http://localhost:9999/bigdata/sparql"
SUBJECT = 'subject'
PREDICATE = 'predicate'
INVERSE_FUNCTIONALITY = 'inverse_functionality'


In [4]:
graph_1_inv_func_df = pd.read_csv(GRAPH_1_INV_FUNC_PATH)

threshold_graph_1_inv_func_df = graph_1_inv_func_df[graph_1_inv_func_df[INVERSE_FUNCTIONALITY] > 0.5]

#graph_1_predicate_list = threshold_graph_1_inv_func_df[PREDICATE].tolist()

graph_1 = Graph()
graph_1.parse(GRAPH_1)

<Graph identifier=N3ee65592845f4ef787f6711e12c397d8 (<class 'rdflib.graph.Graph'>)>

In [5]:
graph_2_inv_func_df = pd.read_csv(GRAPH_2_INV_FUNC_PATH)

threshold_graph_2_inv_func_df = graph_2_inv_func_df[graph_2_inv_func_df[INVERSE_FUNCTIONALITY] > 0.5]

#graph_2_predicate_list = threshold_graph_2_inv_func_df[PREDICATE].tolist()

graph_2 = Graph()
graph_2.parse(GRAPH_2)
#graph_2 = Graph("SPARQLStore")
#graph_2.open(GRAPH_2)

<Graph identifier=Na9220770da9e419bb02fb239d042e083 (<class 'rdflib.graph.Graph'>)>

In [87]:
def get_label_graph(graph, predicate_df):
    predicate_label_list = list()
    LABEL = "http://www.w3.org/2000/01/rdf-schema#label"
    label_predicate = URIRef(LABEL)
    for index, row in tqdm(predicate_df.iterrows(), total=len(predicate_df)):
        search_uriref = URIRef(row['predicate'])
        label = str(next(graph.objects(search_uriref, label_predicate), ""))
        predicate_label_list.append(label)
    return predicate_label_list

predicate_1_list = get_label_graph(graph_1, graph_1_inv_func_df) 
graph_1_inv_func_df['labels'] = predicate_1_list

predicate_2_list = get_label_graph(graph_2, graph_2_inv_func_df) 
graph_2_inv_func_df['labels'] = predicate_2_list

graph_1_predicate_set = set(graph_1_inv_func_df['predicate'])
graph_2_predicate_set = set(graph_2_inv_func_df['predicate'])

predicate_prob_dict = dict()

for predicate_uri in graph_1_predicate_set:
    if predicate_uri in graph_2_predicate_set:
        predicate_prob_dict.setdefault(predicate_uri, {})
        predicate_prob_dict[predicate_uri][predicate_uri] = 1.0


  0%|          | 0/342 [00:00<?, ?it/s]

  0%|          | 0/218 [00:00<?, ?it/s]

In [88]:
def match_predicate_labels(predicate_prob_dict, graph_1_inv_func_df, graph_2_inv_func_df, label_column, max_score):
    graph_2_predicate_labels_dict = {label: list(graph_2_inv_func_df.loc[graph_2_inv_func_df[label_column] == label, 'predicate'])
           for label in graph_2_inv_func_df[label_column].unique()}
    
    del graph_2_predicate_labels_dict['']
    
    for _, row in graph_1_inv_func_df.iterrows():
        label = row[label_column]
        predicate_1 = row['predicate']
        if label in graph_2_predicate_labels_dict:
            for predicate_2 in graph_2_predicate_labels_dict[label]:
                if predicate_1 in predicate_prob_dict.keys() and predicate_2 in predicate_prob_dict[predicate_1].keys():
                    continue
                predicate_prob_dict.setdefault(predicate_1, {})[predicate_2] = max_score

In [89]:
match_predicate_labels(predicate_prob_dict, graph_1_inv_func_df, graph_2_inv_func_df, 'labels', 0.9)

In [90]:
def normalize_string(s):
    # remove punctuation
    s = s.translate(str.maketrans('', '', string.punctuation))
    # split the string at uppercase letters and digits and join with spaces
    s = re.sub(r'([a-z])([A-Z])', r'\1 \2', s)
    s = re.sub(r'([A-Z])([A-Z][a-z])', r'\1 \2', s)
    s = re.sub(r'([a-zA-Z])(\d)', r'\1 \2', s)
    s = re.sub(r'(\d)([a-zA-Z])', r'\1 \2', s)
    # replace underscores with spaces
    s = s.replace('_', ' ')
    # remove multiple consecutive spaces and leading/trailing spaces
    s = ' '.join(s.split()).strip()
    # convert to lowercase and return
    return s.lower()

In [91]:
graph_1_inv_func_df['normalized label'] = graph_1_inv_func_df['labels'].apply(normalize_string)
graph_2_inv_func_df['normalized label'] = graph_2_inv_func_df['labels'].apply(normalize_string)

match_predicate_labels(predicate_prob_dict, graph_1_inv_func_df, graph_2_inv_func_df, 'normalized label', 0.8)

In [92]:
nltk.download('stopwords') # download stop words list

stop_words = set(stopwords.words('english')) # set of English stop words

def remove_stopwords(s):
    words = s.split() # split text into individual words

    filtered_words = [word for word in words if not word.lower() in stop_words] # remove stop words

    filtered_text = ' '.join(filtered_words)
    return filtered_text

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/yamamotobikutorueiichi/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [93]:
LABEL = 'stopword label'

graph_1_inv_func_df[LABEL] = graph_1_inv_func_df['normalized label'].apply(remove_stopwords)
graph_2_inv_func_df[LABEL] = graph_2_inv_func_df['normalized label'].apply(remove_stopwords)

match_predicate_labels(predicate_prob_dict, graph_1_inv_func_df, graph_2_inv_func_df, LABEL, 0.7)

In [94]:
def remove_corpus_specific_stopword(graph_df):
    doc_freq = defaultdict(int)

    for _, row in graph_df.iterrows():
        doc = row['stopword label']
        words = set(word_tokenize(doc))
        for word in words:
            doc_freq[word] += 1
            
    total_docs = len(graph_df)
    corpus_stopwords = set()
    for word, freq in doc_freq.items():
        if freq / total_docs > 0.2: # word appears in more than 20% of documents
            corpus_stopwords.add(word)    
    label_list = list()
    for _, row in graph_df.iterrows():
        words = word_tokenize(row['stopword label'])
        filtered_words = [word for word in words if not word.lower() in corpus_stopwords]
        filtered_text = ' '.join(filtered_words)
        label_list.append(filtered_text)
    
    graph_df['corpus stopword label'] = label_list

In [95]:
remove_corpus_specific_stopword(graph_1_inv_func_df)
remove_corpus_specific_stopword(graph_2_inv_func_df)

LABEL = 'corpus stopword label'

for _, row in graph_1_inv_func_df.iterrows():
    label_1 = row[LABEL]
    predicate_1 = row['predicate']
    if not label_1:
        continue
    
    for _, row_2 in graph_2_inv_func_df.iterrows():
        label_2 = row_2[LABEL]
        predicate_2 = row_2['predicate']
        if not label_2:
            continue
        if not predicate_1 in predicate_prob_dict.keys() or not predicate_2 in predicate_prob_dict[predicate_1]:
            sim = fuzz.WRatio(label_1, label_2) / 100
            prob = 0.6 * sim
            predicate_prob_dict.setdefault(predicate_1, {})[predicate_2] = prob

In [96]:
nltk_tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained("bert-base-uncased")

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [97]:
def embed_long_sentence(long_sentence):
    sentences = nltk_tokenizer.tokenize(long_sentence)
    
    tokens = {'input_ids': [], 'attention_mask': []}

    max_token = 140
    for sentence in sentences:
        new_tokens = tokenizer.encode_plus(sentence, return_tensors="pt", max_length=max_token, padding='max_length')
        tokens['input_ids'].append(new_tokens['input_ids'][0][:max_token])
        tokens['attention_mask'].append(new_tokens['attention_mask'][0][:max_token])

    tokens['input_ids'] = torch.stack(tokens['input_ids'])
    tokens['attention_mask'] = torch.stack(tokens['attention_mask'])
    
    outputs = model(**tokens)
    
    embeddings = outputs.last_hidden_state
    
    attention_mask = tokens['attention_mask']
    
    mask = attention_mask.unsqueeze(-1).expand(embeddings.size()).float()

    masked_embeddings = embeddings * mask
    
    summed = torch.sum(masked_embeddings, 1)

    summed_mask = torch.clamp(mask.sum(1), min=1e-9)

    mean_pooled = summed / summed_mask
    
    return mean_pooled.detach().numpy()

In [98]:
def get_label_vec_dict(df):
    LABEL = 'corpus stopword label'

    df_label_set = set(df[LABEL])
    df_label_vec_dict = dict()

    for label in tqdm(df_label_set):
        if not label:
            continue

        df_label_vec_dict[label] = embed_long_sentence(label)
    return df_label_vec_dict

In [99]:
graph_2_label_vec_dict = get_label_vec_dict(graph_2_inv_func_df)

  0%|          | 0/194 [00:00<?, ?it/s]

In [100]:
LABEL = 'corpus stopword label'

for _, row in tqdm(graph_1_inv_func_df.iterrows(), total=len(graph_1_inv_func_df)):
    label_1 = row[LABEL]
    predicate_1 = row['predicate']
    if not label_1:
        continue
    vec_1 = embed_long_sentence(label_1)
    
    for _, row_2 in graph_2_inv_func_df.iterrows():
        predicate_2 = row_2['predicate']
        label_2 = row_2[LABEL]
        
        if not label_2:
            continue
        
        if predicate_prob_dict[predicate_1][predicate_2] > 0.5:
            continue
        
        vec_2 = graph_2_label_vec_dict[row_2[LABEL]]
        
        similarities = cosine_similarity(vec_1, vec_2)
        max_similarity = max(map(max, similarities))
        prob = 0.5 * max_similarity
        
        if prob > predicate_prob_dict[predicate_1][predicate_2]:
            predicate_prob_dict[predicate_1][predicate_2] = prob

  0%|          | 0/342 [00:00<?, ?it/s]

In [26]:
literal_y1_dict = dict()
used_p1_dict = dict()
graph_1_predicate_list = list()

for index, row in tqdm(threshold_graph_1_inv_func_df.iterrows(), total=len(threshold_graph_1_inv_func_df)):
    predicate = row[PREDICATE]
    predicate_uri = URIRef(predicate)
    
    if sum(1 for _ in graph_1.subject_objects(predicate_uri)) < 5:
        continue
    
    graph_1_predicate_list.append(predicate)
    
    for s, p, o in graph_1.triples((None, predicate_uri, None)):

        if type(o) != Literal or not isinstance(o, Literal) or not (o.datatype is None or o.datatype == XSD.string or o.datatype == RDF.langString):
            continue
        
        o_value = str(o)
        if o_value not in literal_y1_dict.keys():
            literal_y1_dict[o_value] = list()
        y1_value_list = literal_y1_dict[o_value]
        y1_value_list.append({
            SUBJECT: s,
            PREDICATE: predicate_uri
        })

  0%|          | 0/205 [00:00<?, ?it/s]

In [27]:
y2_matches = dict()
graph_2_predicate_list = list()

for index, row in tqdm(threshold_graph_2_inv_func_df.iterrows(), total=len(threshold_graph_2_inv_func_df)):
    predicate = row[PREDICATE]
    predicate_uri = URIRef(predicate)
    
    if sum(1 for _ in graph_2.subject_objects(predicate_uri)) < 5:
        continue
        
    graph_2_predicate_list.append(predicate)
    
    for s, o in graph_2.subject_objects(predicate_uri):
        if type(o) != Literal or not isinstance(o, Literal) or not (o.datatype is None or o.datatype == XSD.string or o.datatype == RDF.langString):
            continue
        
        # Check if exist match
        o_value = str(o)
        if o_value not in literal_y1_dict.keys():
            continue
            
        if o_value not in y2_matches.keys():
            y2_matches[o_value] = list()
        y2_match_list = y2_matches[o_value]
        y2_match_list.append({
            SUBJECT: s,
            PREDICATE: predicate_uri
        })

  0%|          | 0/151 [00:00<?, ?it/s]

In [28]:
def get_predicate_prob(predicate_pair_dict, p1, p2):
    if p1 not in predicate_pair_dict.keys():
        predicate_pair_dict[p1] = dict()
    if p2 not in predicate_pair_dict[p1].keys():
        predicate_pair_dict[p1][p2] = 0.1

    return predicate_pair_dict[p1][p2]

In [29]:
inv_func_1_dict = dict()

for index, row in tqdm(threshold_graph_1_inv_func_df.iterrows(), total=len(threshold_graph_1_inv_func_df)):
    inv_func_1_dict[row['predicate']] = row['inverse_functionality']

  0%|          | 0/205 [00:00<?, ?it/s]

In [30]:
inv_func_2_dict = dict()

for index, row in tqdm(threshold_graph_2_inv_func_df.iterrows(), total=len(threshold_graph_2_inv_func_df)):
    inv_func_2_dict[row['predicate']] = row['inverse_functionality']

  0%|          | 0/151 [00:00<?, ?it/s]

In [31]:
def save_predicate_pair(predicate_pair_counter, x1, p1, y1, x2, p2, y2):
    predicate_pair_counter.append({
        'x1': x1,
        'p1': p1,
        'y1': y1,
        'x2': x2,
        'p2': p2,
        'y2': y2,
    })

In [32]:
def update_prob_entities(entity_pair_match_dict, x1, x2, p1, p2, prob_y):
    if x1 not in entity_pair_match_dict.keys():
        entity_pair_match_dict[x1] = dict()
    if x2 not in entity_pair_match_dict[x1].keys():
        entity_pair_match_dict[x1][x2] = 1
    #if x1 == 'http://dbkwik.webdatacommons.org/finalfantasy./resource/Toad_(Final_Fantasy_V_enemy)':
    #    print(len(entity_pair_match_dict[x1]))
    
    y1_pred = str(p1)
    y2_pred = str(p2)
    pred_prob_1_2 = get_predicate_prob(predicate_pair_dict_1, y1_pred, y2_pred)
    pred_prob_2_1 = get_predicate_prob(predicate_pair_dict_2, y2_pred, y1_pred)

    new_factor = (1-pred_prob_1_2*inv_func_1_dict[y1_pred] * prob_y) * (1-pred_prob_2_1*inv_func_2_dict[y2_pred] * prob_y)

    entity_pair_match_dict[x1][x2] *= new_factor

    return 1 - entity_pair_match_dict[x1][x2]

In [33]:
def calculate_entity_prob_using_attribute(new_entity_pair_match_dict):
    for o_value, y2_match_list in tqdm(y2_matches.items(), desc='Attribute loop', leave=False):
        y1_match_list = literal_y1_dict[o_value]

        for y1_match in y1_match_list:
            y1_subject = y1_match['subject']

            for y2_match in y2_match_list:
                y2_subject = y2_match['subject']


                y1_pred = str(y1_match['predicate'])
                y2_pred = str(y2_match['predicate'])
                sim = update_prob_entities(new_entity_pair_match_dict, str(y1_subject), str(y2_subject),
                                     y1_pred, y2_pred, 1)

                if sim > 0.1:
                    save_predicate_pair(predicate_pair_counter, str(y1_subject), y1_pred, o_value, str(y2_subject),
                                        y2_pred, o_value)
                

In [34]:
def get_inbound_neighbors(graph, predicate_list, y, loaded_neighbors_dict):
    if not y:
        return []
    
    if y in loaded_neighbors_dict.keys():
        return loaded_neighbors_dict[y]
    
    y_url = y
    if type(y_url) != URIRef:
        y_url = URIRef(y)
    
    attempts = 0
    while attempts < 10:
        try:
            neighbor_list = list()
            for s, p in graph.subject_predicates(y_url):
                if str(p) in predicate_list:
                    neighbor_list.append({
                        'p': p,
                        's': s
                    })
            return neighbor_list
        except Exception as e:
            print(e)
            attempts += 1
    loaded_neighbors_dict[y] = neighbor_list
    return neighbor_list

In [35]:
def update_prob_entity_neighbors(entity_pair_dict, y1_neighbors,
                                 y2_neighbors, y_sim, y1, y2):
    for x1 in y1_neighbors:
        for x2 in y2_neighbors:
            x1_str = str(x1['s'])
            x2_str = str(x2['s'])
            p1_str = str(x1['p'])
            p2_str = str(x2['p'])
            sim = update_prob_entities(entity_pair_dict, x1_str, x2_str, p1_str, str(x2['p']),
                                 y_sim)
            if sim > 0.1:
                save_predicate_pair(predicate_pair_counter, x1_str, p1_str, str(y1), x2_str, p2_str, str(y2))

In [36]:
def calculate_entity_prob_using_neighbors(new_entity_pair_dict, old_entity_pair_dict, loaded_neighbors_dict):
    y1_keys = list(old_entity_pair_dict.keys())
    for y1 in tqdm(y1_keys, desc='neighbor loop', leave=False):
        y1_neighbors = get_inbound_neighbors(graph_1, graph_1_predicate_list, y1, loaded_neighbors_dict)
        y2_keys = list(old_entity_pair_dict[y1].keys())
        for y2 in y2_keys:
            y_sim = 1
            if y1 in new_entity_pair_dict.keys() and y2 in new_entity_pair_dict[y1].keys():
                y_sim -= new_entity_pair_dict[y1][y2]
            else:
                y_sim -= old_entity_pair_dict[y1][y2]
            if y_sim < 0.2:
                continue
            
            y2_neighbors = get_inbound_neighbors(graph_2, graph_2_predicate_list, y2, loaded_neighbors_dict)
            update_prob_entity_neighbors(new_entity_pair_dict, y1_neighbors, y2_neighbors, y_sim, y1, y2)
    

In [37]:
def get_prob_entity_pair(entity_pair_match_dict, s1, s2):
    if s1 in entity_pair_match_dict.keys() and s2 in entity_pair_match_dict[s1].keys():
        return 1 - entity_pair_match_dict[s1][s2]
    return 0

In [38]:
def get_set_of_triples_by_predicate(predicate_pair_counter_df, reversed_bool):
    if reversed_bool:
        return predicate_pair_counter_df[['x2', 'p2', 'y2']].drop_duplicates()
    else:
        return predicate_pair_counter_df[['x1', 'p1', 'y1']].drop_duplicates()

In [39]:
def get_columns(reversed_bool):
    if reversed_bool:
        return {
            'x1': 'x2',
            'p1': 'p2',
            'y1': 'y2',
            'x2': 'x1',
            'p2': 'p1',
            'y2': 'y1'
        }
    else:
        return {
            'x1': 'x1',
            'p1': 'p1',
            'y1': 'y1',
            'x2': 'x2',
            'p2': 'p2',
            'y2': 'y2'
        }

In [40]:
def calculate_product(matched_row, entity_pair_match_dict):
    x_sim = 1 - entity_pair_match_dict[matched_row['x1']][matched_row['x2']]
    if matched_row['y1'] == matched_row['y2']:
        y_sim = 1
    else:
        y_sim = entity_pair_match_dict[matched_row['y1']][matched_row['y2']]
    return 1 - x_sim * y_sim

In [41]:
def calculate_sum_by_triple(indexed_df, triple_row):
    matched_triples = indexed_df.join(triple_row)
    return 1.0 - numpy.product(matched_triples['product_element'])

In [42]:
def calculate_upper_sum(entity_pair_match_dict, predicate_pair_counter_df, unique_triples, p1, p2, reversed_bool):
    columns = get_columns(reversed_bool)
    
    filtered_by_ps_df = predicate_pair_counter_df[predicate_pair_counter_df[columns['p2']].isin([p2])]
    
    grouped_df = filtered_by_ps_df.groupby([columns['x1'], columns['y1']])
    product = grouped_df['product_element'].prod()
    return (1 - product).sum()

In [43]:
def calculate_lower_sum(entity_pair_match_dict, predicate_pair_counter_df, unique_triples, p1, reversed_bool):
    columns = get_columns(reversed_bool)
    
    grouped_df = predicate_pair_counter_df.groupby([columns['x1'], columns['y1']])
    product = grouped_df['product_element'].prod()
    
    return (1 - product).sum()

In [44]:
def calculate_x_sim(x1, x2, entity_pair_match_dict, reversed_bool):
    if reversed_bool:
        return 1 - entity_pair_match_dict[x2][x1]
    return 1 - entity_pair_match_dict[x1][x2]

In [45]:
def calculate_y_sim(y1, y2, entity_pair_match_dict, reversed_bool):
    if y1 == y2:
        return 1
    else:
        if reversed_bool:
            if y2 in entity_pair_match_dict.keys() and y1 in entity_pair_match_dict[y2].keys():
                return 1 - entity_pair_match_dict[y2][y1]
        if y1 in entity_pair_match_dict.keys() and y2 in entity_pair_match_dict[y1].keys():
            return 1 - entity_pair_match_dict[y1][y2]
    return 0

In [111]:
def calculate_sub_predicates(predicate_sub_relation, predicate_pair_dict, predicate_pair_counter, entity_pair_match_dict, reversed_bool):
    columns = get_columns(reversed_bool)
    predicate_pair_counter_df = pd.DataFrame(predicate_pair_counter)
    
    predicate_pair_counter_df['x_sim'] = predicate_pair_counter_df.apply(lambda x: calculate_x_sim(x[columns["x1"]], x[columns["x2"]], entity_pair_match_dict, reversed_bool), axis=1)
    predicate_pair_counter_df['y_sim'] = predicate_pair_counter_df.apply(lambda x: calculate_y_sim(x[columns["y1"]], x[columns["y2"]], entity_pair_match_dict, reversed_bool), axis=1)

    predicate_pair_counter_df['product_element'] = predicate_pair_counter_df.apply(lambda x: 1.0 - x['x_sim'] * x['y_sim'], axis=1)

    for p1 in tqdm(predicate_pair_dict.keys(), desc='Predicate loop', leave=False):
        filtered_counter = predicate_pair_counter_df[predicate_pair_counter_df[columns['p1']].isin([p1])]
        if len(filtered_counter) < 10:
            for p2 in predicate_pair_dict[p1].keys():
                predicate_sub_relation.setdefault(p1, {})[p2] = 0.0
        unique_triples = get_set_of_triples_by_predicate(filtered_counter, reversed_bool)
        for p2 in predicate_pair_dict[p1].keys():
            predicate_sub_relation.setdefault(p1, {})[p2] = calculate_upper_sum(entity_pair_match_dict, filtered_counter, unique_triples, p1,
                                                              p2, reversed_bool)
        
        lower_sum = calculate_lower_sum(entity_pair_match_dict, filtered_counter, unique_triples, p1, reversed_bool)
        if lower_sum == 0.0:
            continue
        for p2 in predicate_sub_relation[p1].keys():
            predicate_sub_relation[p1][p2] /= lower_sum
            
            

In [47]:
def get_subject_object(graph, predicate):
    attempts = 0
    while attempts < 10:
        try:
            s_o_list = list()
            for s, o in graph.subject_objects(URIRef(predicate)):
                s_o_list.append({
                        'subject': s,
                        'object': o
                    })
            return s_o_list
        except Exception as e:
            print(e)
            attempts += 1
    
    return s_o_list

In [48]:
def check_if_string(y):
    return type(y) == Literal and y.value and type(y.value) == str

In [49]:
def calculate_sub_pred_product(entity_pair_match_dict, x1, x2, y1, y2):
    if check_if_string(y1) and check_if_string(y2):
        if y1.value != y2.value:
            return 0.0
        y_value = y1.value
        if y_value not in literal_y1_dict.keys() or y_value not in y2_matches.keys():
            return 0.0
        return entity_pair_match_dict[str(x1)][str(x2)]
    return 0.0

In [54]:
def save_entity_pairs(i, entity_pair_match_dict):
    entity_pair_sim_list = list()
    for y1 in entity_pair_match_dict.keys():
        for y2 in entity_pair_match_dict[y1].keys():
            similarity = 1 - entity_pair_match_dict[y1][y2]
            entity_pair_sim_list.append({
                "e1": y1,
                "e2": y2,
                "sim": similarity
            })
    entity_sim_df = pd.DataFrame(entity_pair_sim_list)
    entity_sim_df.to_csv("ma-se-pre-calc-pred/entity_sim_" + str(i) + ".csv")

In [55]:
def save_predicate_pairs_into_df(i, predicate_pair_dict, name):
    predicate_pair_list = list()
    for p1 in predicate_pair_dict.keys():
        for p2 in predicate_pair_dict[p1].keys():
            predicate_pair_list.append({
                "p1": p1,
                "p2": p2,
                "sim": predicate_pair_dict[p1][p2]
            })
    predicate_pair_df = pd.DataFrame(predicate_pair_list)
    predicate_pair_df.to_csv(name + str(i) + ".csv")

In [104]:
def pre_calc_pred_pair_dict(predicate_prob_dict, pred_sub_relation, reversed_bool):
    new_predicate_pair_dict = dict()
    
    for pred_1, pred_2_dict in pred_sub_relation.items():
        for pred_2 in pred_2_dict:
            if reversed_bool:
                if pred_1 not in new_predicate_pair_dict.get(pred_2, {}):
                    new_predicate_pair_dict.setdefault(pred_2, {})[pred_1] = 0
                new_predicate_pair_dict[pred_2][pred_1] += 0.5 * pred_sub_relation[pred_1][pred_2]
            else:
                if pred_2 not in new_predicate_pair_dict.get(pred_1, {}):
                    new_predicate_pair_dict.setdefault(pred_1, {})[pred_2] = 0
                new_predicate_pair_dict[pred_1][pred_2] += 0.5 * pred_sub_relation[pred_1][pred_2]

    for pred_1 in predicate_prob_dict:
        for pred_2 in predicate_prob_dict[pred_1]:
            if reversed_bool:
                if pred_1 not in new_predicate_pair_dict.get(pred_2, {}):
                    new_predicate_pair_dict.setdefault(pred_2, {})[pred_1] = 0
                new_predicate_pair_dict[pred_2][pred_1] += 0.5 * predicate_prob_dict[pred_1][pred_2]
            else:
                if pred_2 not in new_predicate_pair_dict.get(pred_1, {}):
                    new_predicate_pair_dict.setdefault(pred_1, {})[pred_2] = 0
                new_predicate_pair_dict[pred_1][pred_2] += 0.5 * predicate_prob_dict[pred_1][pred_2]

    return new_predicate_pair_dict

In [112]:
old_entity_pair_match_dict = dict()
loaded_neighbors_dict = dict()
pred_sub_relation_1 = dict()
pred_sub_relation_2 = dict()

for i in tqdm(range(10), desc='Main loop'):
    predicate_pair_dict_1 = pre_calc_pred_pair_dict(predicate_prob_dict, pred_sub_relation_1, False)
    predicate_pair_dict_2 = pre_calc_pred_pair_dict(predicate_prob_dict, pred_sub_relation_2, True)
    predicate_pair_counter = list()
    
    save_predicate_pairs_into_df(i, predicate_pair_dict_1, "ma-se-pre-calc-pred/predicate_pair_1_")
    save_predicate_pairs_into_df(i, predicate_pair_dict_2, "ma-se-pre-calc-pred/predicate_pair_2_")

    new_entity_pair_match_dict = dict()
    
    calculate_entity_prob_using_attribute(new_entity_pair_match_dict)     
    
    calculate_entity_prob_using_neighbors(new_entity_pair_match_dict, old_entity_pair_match_dict, loaded_neighbors_dict)

    #calculate_prob_predicates(predicate_pair_dict, new_entity_pair_match_dict)
    calculate_sub_predicates(pred_sub_relation_1, predicate_pair_dict_1, predicate_pair_counter, new_entity_pair_match_dict, False)
    calculate_sub_predicates(pred_sub_relation_2, predicate_pair_dict_2, predicate_pair_counter, new_entity_pair_match_dict, True)
    
    save_entity_pairs(i, new_entity_pair_match_dict)
    old_entity_pair_match_dict = new_entity_pair_match_dict

Main loop:   0%|          | 0/10 [00:00<?, ?it/s]

Attribute loop:   0%|          | 0/11007 [00:00<?, ?it/s]

neighbor loop: 0it [00:00, ?it/s]

Predicate loop:   0%|          | 0/337 [00:00<?, ?it/s]

Predicate loop:   0%|          | 0/213 [00:00<?, ?it/s]

...

Predicate loop:   0%|          | 0/534 [00:00<?, ?it/s]

Attribute loop:   0%|          | 0/11007 [00:00<?, ?it/s]

neighbor loop:   0%|          | 0/15271 [00:00<?, ?it/s]

Predicate loop:   0%|          | 0/337 [00:00<?, ?it/s]

Predicate loop:   0%|          | 0/534 [00:00<?, ?it/s]

In [101]:
predicate_prob_dict

{'http://www.w3.org/2004/02/skos/core#prefLabel': {'http://www.w3.org/2004/02/skos/core#prefLabel': 1.0},
 'http://purl.org/dc/terms/subject': {'http://purl.org/dc/terms/subject': 1.0},
 'http://dbkwik.webdatacommons.org/ontology/thumbnail': {'http://dbkwik.webdatacommons.org/ontology/thumbnail': 1.0},
 'http://www.w3.org/2000/01/rdf-schema#comment': {'http://www.w3.org/2000/01/rdf-schema#comment': 1.0},
 'http://dbkwik.webdatacommons.org/ontology/wikiPageWikiLink': {'http://dbkwik.webdatacommons.org/ontology/wikiPageWikiLink': 1.0},
 'http://www.w3.org/2004/02/skos/core#broader': {'http://www.w3.org/2004/02/skos/core#broader': 1.0},
 'http://xmlns.com/foaf/0.1/thumbnail': {'http://xmlns.com/foaf/0.1/thumbnail': 1.0},
 'http://dbkwik.webdatacommons.org/ontology/abstract': {'http://dbkwik.webdatacommons.org/ontology/abstract': 1.0},
 'http://xmlns.com/foaf/0.1/depiction': {'http://xmlns.com/foaf/0.1/depiction': 1.0},
 'http://dbkwik.webdatacommons.org/ontology/wikiPageWikiLinkText': {'h